In [7]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from datetime import datetime as dt
import datetime
import quandl
import math
from statsmodels.stats.diagnostic import het_arch
from arch import arch_model
from pypfopt import EfficientFrontier,objective_functions
from sklearn.decomposition import PCA
from sklearn.mixture import GaussianMixture
from sklearn.cluster import KMeans
from sklearn import metrics
from copy import deepcopy

In [8]:
import sklearn
sklearn.__version__

'1.2.2'

In [9]:
from pandas_datareader import data as pdr
import yfinance as yf
yf.pdr_override()

In [10]:
def modify_date(date):
    return date[:10]

In [11]:
def data_cleaning(data):
    if (data.isna()).any().any():
        missing = np.where(data.isna())
        rows=missing[0]
        cols=missing[1]
        print(rows)
        for row in range(len(rows)):
            col=cols[row]
            if row == len(data)-1:
                data.iloc[row,col]=data.iloc[row-1,col]**2/data.iloc[row-2,col]
            elif row ==0:
                data.iloc[row,col]=data.iloc[row+1,col]**2/data.iloc[row+2,col]
            else:
                data.iloc[row,col]=math.sqrt(data.iloc[row-1,col]*data.iloc[row+1,col])
        print(data)

In [14]:
def get_price_years_ago(data, date,time):
    year_ago=date-datetime.timedelta(days=int(time*365))
    price_year_ago=data[data.index<=year_ago]
    return price_year_ago

In [15]:
def max_drawdown_absolute(returns):
    r = returns.add(1).cumprod()
    dd = r.div(r.cummax()).sub(1)
    mdd = dd.min()
    end = dd.argmin()
    start = r.iloc[:end].argmax()
    return abs(mdd), start, end

In [16]:
def fit_garch(data,p,q):
    lag = max(p,q)
    length =res.shape[0]
    am = arch_model(res, vol='Garch', p=1, o=0, q=1, dist='Normal')
    split_date = one_year_monthly_return.index.values[lag-1]
    results = am.fit(last_obs=split_date)
    forecasts = results.forecast(horizon=1, start = length-lag, method='simulation', simulations=1000)
    sims = forecasts.variance
    std = np.sqrt(np.sum(sims)*12/lag)
    return std

In [17]:
def post_allocation(dfMVOweight):

    dfMVOweight['equal']=1/len(dfMVOweight)
    numofstocks=len(dfMVOweight)
    allocationweight=allocation.loc[numofstocks,:]
    dfMVOweight['proportion']=''
    dfMVOweight['adjusted proportion']=''
    dfMVOweight['direct']=''
    residual=0
    for i in range(numofstocks):
        dfMVOweight.iloc[i,4]=dfMVOweight.iloc[i,1]/np.sum(dfMVOweight['PR_SR'])
        if (dfMVOweight.iloc[i,4]+residual/(numofstocks-i))>allocationweight[0]:
            dfMVOweight.iloc[i,5]=allocationweight[0]
        else:
            dfMVOweight.iloc[i,5]=(dfMVOweight.iloc[i,4]+residual/(numofstocks-i))
        residual+=dfMVOweight.iloc[i,4]-dfMVOweight.iloc[i,5]
    for i in range(int(allocationweight[1])):
        dfMVOweight.iloc[i,6]=allocationweight[0]
    for i in range(int(allocationweight[1]),int(allocationweight[1]+allocationweight[3])):
        dfMVOweight.iloc[i,6]=allocationweight[2]
    return dfMVOweight

In [18]:
def output(weight):
    if stock_type == "S&P100":
        OEX=pdr.get_data_yahoo("^OEX", start=start_swan_date, end=end_swan_date)["Adj Close"]

    elif stock_type == "S&P500":
        OEX=pdr.get_data_yahoo("SPY", start=start_swan_date, end=end_swan_date)["Adj Close"]

    stock_price=pdr.get_data_yahoo(list(weight.index), start=start_swan_date, end=end_swan_date)["Adj Close"]
    OEX.to_csv("oex.csv")
    injected_result = pd.DataFrame(index = stock_price.index )
    S1=np.array(10000*weight.T)/np.array(stock_price.iloc[0,:]).T
    portfolio_value = stock_price@S1.T
    injected_result["portfolio_value"]=portfolio_value
    S2 = 10000/float(OEX[0])
    injected_result["oex"]=S2*OEX
    return injected_result

# Step 1 - Preselection

In [19]:
# Preselection parameters set up
method = "db"          # or avg or anyother method
stock_type = "S&P100"
end_swan = "Swan10a"         #equals the last swan before the swan we are going to predict
start_swan="Swan4"
start = dt(2019,1,1)
end = dt(2022,1,1)
selected_stock_number = 22     #number of stock preselected
start_swan_date = dt(2022,1,3)
end_swan_date = dt(2023,1,3)
w1 = 0.17
w2 = 0.17
MA_days = 30
N = 7 # This parameter is set to help classification method like K-means

In [20]:
#read all stocks and their swan beta
if stock_type == "S&P100":
    portfolio_beta = pd.read_excel("All_SwanBeta100.xlsx",index_col=0)
else:
    portfolio_beta = pd.read_excel("All_SwanBeta500.xlsx",index_col=0)

In [21]:
selected_swans_var=portfolio_beta.loc[:,start_swan:end_swan]
portfolio_beta =portfolio_beta[ selected_swans_var.T.isnull().sum()<selected_swans_var.shape[1]-1]

In [22]:
portfolio_beta

Swan-3    Swan-2    Swan-1     Swan1     Swan2     Swan3     Swan4  \
Ticker                                                                         
CHTR         NaN       NaN       NaN       NaN       NaN       NaN       NaN   
GM           NaN       NaN       NaN       NaN       NaN       NaN       NaN   
KMI          NaN       NaN       NaN       NaN       NaN       NaN       NaN   
GOOG         NaN       NaN       NaN       NaN       NaN       NaN       NaN   
GOOGL        NaN       NaN       NaN       NaN       NaN       NaN       NaN   
...          ...       ...       ...       ...       ...       ...       ...   
UNP     0.850695  2.127809  1.993802  1.088334  0.427848  0.418409  0.283910   
USB     0.407208  0.375769  0.483245  0.176170  1.187362  1.307068  0.811824   
WFC     1.388900  1.261192  1.686449  0.558622  1.587780  1.233240  0.300985   
WMT     0.897873 -1.424131  0.462878  1.059818  1.484265  0.762944  0.586029   
XOM     1.007288  0.845021 -0.532604  0.914433  0.008834  0.475580  0.716433   

           Swan5     Swan6     Swan7     Swan8     Swan9   Swan10a   Swan10b  
Ticker                                                                        
CHTR         NaN  1.583170  0.649030  0.797374  0.939407  1.060138  1.278190  
GM           NaN  2.026711  0.792127  0.190040  1.553517  2.447747  1.934870  
KMI          NaN  0.540529  1.230239  0.919927  1.592887 -1.141071 -0.541752  
GOOG    0.803565  1.167641  0.916183  0.944312  0.976498  0.875866  1.104899  
GOOGL   0.803565  1.167641  0.870361  0.938163  0.979057  0.880849  1.117074  
...          ...       ...       ...       ...       ...       ...       ...  
UNP     1.275539  1.334344  1.354688  1.049957  1.188887 -0.200038  0.632258  
USB     1.672467  0.905422  0.995170  0.906766  1.495656  0.501194  0.825853  
WFC     1.698834  1.182443  0.995686  0.827634  1.470901  0.571633  1.078228  
WMT     0.461023  0.235666  0.982186  0.414455  0.078002  0.291725  0.710631  
XOM     0.396490  0.938817  1.138592  1.161731  1.518454 -2.833257 -2.305610  

[95 rows x 14 columns]

In [23]:
corr=portfolio_beta.corr()
selected_corr=corr.loc["Swan1":end_swan,"Swan1":end_swan]
corr1={}
for i in range(selected_corr.shape[1]):
    for j in range(i+1,selected_corr.shape[0]):
        selected_corr.iloc[j,i]=np.nan

In [24]:
selected_corr

Swan1     Swan2     Swan3     Swan4     Swan5     Swan6     Swan7  \
Swan1      1.0 -0.004268  0.111982  0.050073  0.001444  0.101963  0.079685   
Swan2      NaN  1.000000  0.549511  0.335485  0.410861  0.392490  0.033937   
Swan3      NaN       NaN  1.000000  0.151778  0.258652  0.435457  0.243705   
Swan4      NaN       NaN       NaN  1.000000 -0.032138  0.143125  0.147027   
Swan5      NaN       NaN       NaN       NaN  1.000000  0.444474  0.221512   
Swan6      NaN       NaN       NaN       NaN       NaN  1.000000  0.301317   
Swan7      NaN       NaN       NaN       NaN       NaN       NaN  1.000000   
Swan8      NaN       NaN       NaN       NaN       NaN       NaN       NaN   
Swan9      NaN       NaN       NaN       NaN       NaN       NaN       NaN   
Swan10a    NaN       NaN       NaN       NaN       NaN       NaN       NaN   

            Swan8     Swan9   Swan10a  
Swan1    0.076826  0.037902 -0.051585  
Swan2    0.307858  0.035989  0.412956  
Swan3    0.224528  0.103467  0.297051  
Swan4    0.225411  0.088824  0.271980  
Swan5    0.208068  0.564402 -0.048352  
Swan6    0.482711  0.404329  0.087378  
Swan7    0.185835  0.164183 -0.119691  
Swan8    1.000000  0.236622 -0.093087  
Swan9         NaN  1.000000 -0.351039  
Swan10a       NaN       NaN  1.000000

In [25]:
avg=selected_corr.mean(axis=1)
weight_swan = avg/sum(avg)
selected_beata=portfolio_beta.loc[:,start_swan:end_swan].fillna(0)
#portfolio_beta["corr_beta"]=selected_beata@weight_swan
#portfolio_beta=portfolio_beta.sort_values(by=["corr_beta"])

In [26]:
portfolio_beta

Swan-3    Swan-2    Swan-1     Swan1     Swan2     Swan3     Swan4  \
Ticker                                                                         
CHTR         NaN       NaN       NaN       NaN       NaN       NaN       NaN   
GM           NaN       NaN       NaN       NaN       NaN       NaN       NaN   
KMI          NaN       NaN       NaN       NaN       NaN       NaN       NaN   
GOOG         NaN       NaN       NaN       NaN       NaN       NaN       NaN   
GOOGL        NaN       NaN       NaN       NaN       NaN       NaN       NaN   
...          ...       ...       ...       ...       ...       ...       ...   
UNP     0.850695  2.127809  1.993802  1.088334  0.427848  0.418409  0.283910   
USB     0.407208  0.375769  0.483245  0.176170  1.187362  1.307068  0.811824   
WFC     1.388900  1.261192  1.686449  0.558622  1.587780  1.233240  0.300985   
WMT     0.897873 -1.424131  0.462878  1.059818  1.484265  0.762944  0.586029   
XOM     1.007288  0.845021 -0.532604  0.914433  0.008834  0.475580  0.716433   

           Swan5     Swan6     Swan7     Swan8     Swan9   Swan10a   Swan10b  
Ticker                                                                        
CHTR         NaN  1.583170  0.649030  0.797374  0.939407  1.060138  1.278190  
GM           NaN  2.026711  0.792127  0.190040  1.553517  2.447747  1.934870  
KMI          NaN  0.540529  1.230239  0.919927  1.592887 -1.141071 -0.541752  
GOOG    0.803565  1.167641  0.916183  0.944312  0.976498  0.875866  1.104899  
GOOGL   0.803565  1.167641  0.870361  0.938163  0.979057  0.880849  1.117074  
...          ...       ...       ...       ...       ...       ...       ...  
UNP     1.275539  1.334344  1.354688  1.049957  1.188887 -0.200038  0.632258  
USB     1.672467  0.905422  0.995170  0.906766  1.495656  0.501194  0.825853  
WFC     1.698834  1.182443  0.995686  0.827634  1.470901  0.571633  1.078228  
WMT     0.461023  0.235666  0.982186  0.414455  0.078002  0.291725  0.710631  
XOM     0.396490  0.938817  1.138592  1.161731  1.518454 -2.833257 -2.305610  

[95 rows x 14 columns]

In [30]:
if method == "gamma":
    portfolio_beta["avg"]=portfolio_beta.loc[:,start_swan:end_swan].mean(axis=1)
    portfolio_beta["avg_sd"]=portfolio_beta.loc[:,start_swan:end_swan].mean(axis=1)+portfolio_beta.loc[:,start_swan:end_swan].std(axis=1,ddof=0)
    portfolio_beta=portfolio_beta.sort_values(by=["avg_sd"])
    preselected_stock = portfolio_beta.iloc[:selected_stock_number,:]
elif method =="average":
    portfolio_beta["avg"]=portfolio_beta.loc[:,start_swan:end_swan].mean(axis=1)
    #Select 18 stocks
    portfolio_beta=portfolio_beta.sort_values(by=["avg"])
    preselected_stock = portfolio_beta.iloc[:selected_stock_number,:]

elif method == "K_means":
    selected_beta =portfolio_beta.loc[:,start_swan:end_swan].dropna()
    Y_predic = selected_beta[end_swan].copy()
    Kmean = KMeans(n_clusters=N,random_state=1,n_init=10)#set the random_state to keep modeling the same every run
    Kmean.fit(selected_beta)
    ct = Kmean.cluster_centers_
    labels = Kmean.labels_
    current_dbscore=metrics.davies_bouldin_score(selected_beta, labels)
    print(current_dbscore)
    selected_beta["Group"]=Kmean.labels_
    print(selected_beta['Group'])
    res = ct.mean(axis=1)
    res [res<0]=0

    min_group = np.where(res==min(res))
    for i in range(N):
        Y_predic[selected_beta["Group"] == i] = res [i]
    selected_beta ["avg"]=Y_predic.values
    selected_beta=selected_beta.sort_values(by=["avg"])
    first_group=selected_beta[selected_beta["Group"]==selected_beta["Group"][0]]
    if first_group.shape[0] <10:
        second_group = selected_beta[selected_beta["Group"]==selected_beta["Group"][first_group.shape[0]]]
        preselected_stock = pd.concat([first_group,second_group],axis=0,ignore_index=True)
    else:
        preselected_stock = first_group
        
elif method == "gpt":
    tickers = ['AMZN', 'AAPL', 'MSFT', 'GOOGL', 'NVDA', 'NFLX', 'MA', 'V', 'UNH', 'JPM', 'GS', 'COST', 'HD', 'TGT', 'ADBE', 'BAC', 'LMT', 'BRK-B']
    preselected_stock = portfolio_beta.loc[tickers, start_swan:end_swan]
    preselected_stock["avg"] = preselected_stock.loc[:, start_swan:end_swan].mean(axis=1)
    print("Selected Stocks (GPT):")
    for _, row in preselected_stock.iterrows():
        print(f"Ticker: {row.name}, Average: {row['avg']}")
    print("=" * 50)
    
elif method == "gptLowest8":
    tickers =  ['AMZN', 'AAPL', 'MSFT', 'GOOGL', 'NVDA', 'NFLX', 'MA', 'V', 'UNH', 'JPM', 'GS', 'COST', 'HD', 'TGT', 'ADBE', 'BAC', 'LMT', 'BRK-B']
    preselected_stock = portfolio_beta.loc[tickers, start_swan:end_swan]
    preselected_stock["avg"] = preselected_stock.loc[:, start_swan:end_swan].mean(axis=1)
    print("Selected Stocks (GPT):")
    for _, row in preselected_stock.iterrows():
        print(f"Ticker: {row.name}, Average: {row['avg']}")
    print("=" * 50)

elif method == "db":
    selected_beta =portfolio_beta.loc[:,start_swan:end_swan].dropna()
    Y_predic = selected_beta[end_swan].copy()
    dbscore_tracker = []
    for R in range(1, 1001):  # Loop through random seeds
        Kmean = KMeans(n_clusters=N,random_state=1,n_init=10)#set the random_state to keep modeling the same every run
        Kmean.fit(selected_beta)
        ct = Kmean.cluster_centers_
        labels = Kmean.labels_
        current_dbscore=metrics.davies_bouldin_score(selected_beta, labels)
        print(current_dbscore)
        selected_beta["Group"]=Kmean.labels_
        print(selected_beta['Group'])
        res = ct.mean(axis=1)
        res [res<0]=0
        
        min_group = np.where(res==min(res))
        for i in range(N):
            Y_predic[selected_beta["Group"] == i] = res [i]
            selected_beta ["avg"]=Y_predic.values
            selected_beta=selected_beta.sort_values(by=["avg"])
            first_group=selected_beta[selected_beta["Group"]==selected_beta["Group"][0]]
        if first_group.shape[0] <10:
            second_group = selected_beta[selected_beta["Group"]==selected_beta["Group"][first_group.shape[0]]]
            preselected_stock = pd.concat([first_group,second_group],axis=0,ignore_index=True)
        else:
            preselected_stock = first_group

        

    

/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isi

1.2208939491534665Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.

Ticker
ACN     5
BKNG    5
BLK     1
GS      1
MDLZ    2
       ..
UNP     0
USB     0
WFC     0
WMT     6
XOM     4
Name: Group, Length: 86, dtype: int32
0.8868778405082505
Ticker
CMCSA    0
MSFT     0
ORCL     0
DUK      6
MMM      4
        ..
AIG      3
SO       4
COP      2
TGT      0
OXY      2
Name: Group, Length: 86, dtype: int32
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
0.8607891980910638
Ticker
PG      3
AAPL    1
JPM     6
C       6
TGT     1
       ..
DHR     1
F       6
AMZN    3
GS      6
FDX     6
Name:

/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_72976/2768151794.py:77: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future versio

0.8441307079431235Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.

Ticker
BRK-B    2
ALL      6
ADBE     3
ABT      1
MDLZ     1
        ..
DD       0
BK       0
HON      0
DUK      2
COP      4
Name: Group, Length: 86, dtype: int32
0.8758317400929924
Ticker
OXY     0
PEP     4
BAC     2
COST    3
JNJ     3
       ..
PFE     1
DD      2
BK      2
GS      2
DIS     2
Name: Group, Length: 86, dtype: int32
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
0.9769374724350044
Ticker
MO      3
CVX     1
RTX     2
LOW     6
MCD     6
       ..
BKNG    4
TXN     4
VZ      3
AMZN    6
DD      0
Name:

/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_72976/2768151794.py:77: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future versio

...

/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_72976/2768151794.py:77: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future versio

0.9283788145886847Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.

Ticker
WFC     6
DD      3
T       0
NVDA    5
INTC    0
       ..
DUK     1
NKE     0
BKNG    5
DIS     3
FDX     3
Name: Group, Length: 86, dtype: int32
0.9239497118480374
Ticker
MSFT    2
KO      4
MRK     6
GILD    2
VZ      6
       ..
INTC    2
PG      4
UNH     4
BA      1
AIG     3
Name: Group, Length: 86, dtype: int32
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
0.9394571944685659
Ticker
F       4
MRK     2
CSCO    1
FDX     4
SO      5
       ..
GS      4
NKE     1
WMT     2
CVS     2
PFE     1
Name: Group, Len

/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:767: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if not hasattr(array, "sparse") and array.dtypes.apply(is_sparse).any():
/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:605: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype):
/Users/wenyiye/anaconda3/lib/python3.11/site-packages/sklearn/utils/validation.py:614: FutureWarning: is_sparse is deprecated and will be removed in a future version. Check `isinstance(dtype, pd.SparseDtype)` instead.
  if is_sparse(pd_dtype) or not is_extension_array_dtype(pd_dtype):
/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_72976/2768151794.py:77: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future versio

0.9134840541883749Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.

Ticker
UNH      4
INTC     6
NKE      6
F        1
WFC      5
        ..
ABT      4
JNJ      0
VZ       0
AXP      5
CMCSA    6
Name: Group, Length: 86, dtype: int32
0.9126951563823335
Ticker
MO       1
LMT      3
RTX      5
TMO      0
NEE      2
        ..
PG       2
LLY      1
BRK-B    1
MDT      2
HON      6
Name: Group, Length: 86, dtype: int32
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
1.0606630537132202
Ticker
BA      4
XOM     3
AAPL    0
COP     3
C       4
       ..
NVDA    5
GILD    0
UPS     2
AMZN    2
BAC 

/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_72976/2768151794.py:77: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  first_group=selected_beta[selected_beta["Group"]==selected_beta["Group"][0]]
/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_72976/2768151794.py:77: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  first_group=selected_beta[selected_beta["Group"]==selected_beta["Group"][0]]
/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_72976/2768151794.py:77: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be trea

In [208]:
preselected_stock.to_csv('temp.csv')

In [209]:
#portfolio_beta["avg"]=portfolio_beta.loc[:,start_swan:end_swan]*weight

In [210]:
preselected_stock["PR"]=1-preselected_stock["avg"]
preselected_stock.head(selected_stock_number)

Swan4     Swan5     Swan6     Swan7     Swan8     Swan9   Swan10a  \
Ticker                                                                         
AMZN   -0.445606  0.328167  0.123350  0.334033  1.561997  0.390752  1.440979   
AAPL    1.345472  0.858909  0.279703  1.582785  1.829198  0.972646  0.955996   
MSFT    0.870338  0.976788  0.607971  0.988753  0.897603  0.868731  1.244157   
GOOGL        NaN  0.803565  1.167641  0.870361  0.938163  0.979057  0.880849   
NVDA    2.545656  0.635717  1.251062 -0.253400  2.787430  1.026747  2.039407   
NFLX         NaN -0.513562  3.473958  0.612869  1.902424  0.212860  3.055209   
MA           NaN  0.644202  0.061049  0.805387  1.084036  1.300211  1.081897   
V            NaN  0.578961  0.335963  0.580043  0.919773  1.153300  0.948281   
UNH    -0.619292  0.706054  1.079657  0.775080  0.688288  1.138551  0.409690   
JPM     1.649017  1.453522  1.887942  1.012903  0.969233  1.348489  1.440874   
GS      1.029728  1.064879  1.959793  1.207118  1.557229  1.356818  1.301592   
COST    0.829818  0.976294 -0.015790  0.618966  0.918643  0.368083  0.536185   
HD      1.546126  0.638987  0.756432  0.161429  1.098092  1.043489  1.605762   
TGT     1.178804  1.162603  0.421476  0.869800  1.393401  0.559241  0.684464   
ADBE    1.599366  1.393154  1.278684  0.687330  1.210366  0.628947  1.680628   
BAC     0.594106  2.142401  2.667373  1.184257  1.192921  1.509426  1.144357   
LMT     0.009892  1.091646  0.569952  0.224948  1.448131  1.138289 -1.969023   
BRK-B   0.220942  1.172896  0.533684  0.870710  0.663086  0.928445 -0.420873   

             avg        PR  
Ticker                      
AMZN    0.533381  0.466619  
AAPL    1.117816 -0.117816  
MSFT    0.922049  0.077951  
GOOGL   0.939939  0.060061  
NVDA    1.433231 -0.433231  
NFLX    1.457293 -0.457293  
MA      0.829464  0.170536  
V       0.752720  0.247280  
UNH     0.596861  0.403139  
JPM     1.394569 -0.394569  
GS      1.353880 -0.353880  
COST    0.604600  0.395400  
HD      0.978617  0.021383  
TGT     0.895684  0.104316  
ADBE    1.211211 -0.211211  
BAC     1.490692 -0.490692  
LMT     0.359119  0.640881  
BRK-B   0.566984  0.433016

# Step 2 - Download data and adjuste price based on Swan Beta

In [211]:
#next line is used to input preselected stock from excel, if you are going to preselect by your self, use this blocks and note next one.
#selected_stock_list =  pd.read_excel("19_stickers.xlsx",header = None).values[:,0]
#swan_beta=pd.read_excel("19_stickers.xlsx",header = None,index_col=0).iloc[:,0]

In [212]:
#Set the paramter to download tradeinfo from Yahoo Finance
selected_stock=preselected_stock
selected_stock_list=selected_stock.index.values
swan_beta=preselected_stock.loc[selected_stock_list,"avg"]

In [213]:
#download data from yahoo finance
yahooDataFrame= pdr.get_data_yahoo(list(selected_stock_list), start=start, end=end)["Adj Close"]

[*********************100%%**********************]  18 of 18 completed


In [214]:
yahooDataFrame

AAPL        ADBE        AMZN        BAC       BRK-B  \
Date                                                                    
2019-01-02   37.845036  224.570007   76.956497  22.099756  202.800003   
2019-01-03   34.075405  215.699997   75.014000  21.745596  191.660004   
2019-01-04   35.530045  226.190002   78.769501  22.648714  195.199997   
2019-01-07   35.450966  229.259995   81.475502  22.631002  196.910004   
2019-01-08   36.126770  232.679993   82.829002  22.586733  196.309998   
...                ...         ...         ...        ...         ...   
2021-12-27  178.065643  577.679993  169.669495  42.306969  296.670013   
2021-12-28  177.038712  569.359985  170.660995  42.363827  298.290009   
2021-12-29  177.127594  569.289978  169.201004  42.297478  299.459991   
2021-12-30  175.962418  570.530029  168.644501  42.202713  299.980011   
2021-12-31  175.340317  567.059998  166.716995  42.164803  299.000000   

                  COST       GOOGL          GS          HD         JPM  \
Date                                                                     
2019-01-02  187.163452   52.734001  152.752380  152.431381   84.811691   
2019-01-03  183.196442   51.273499  150.514771  149.071732   83.606354   
2019-01-04  188.516312   53.903500  155.433945  153.501190   86.688553   
2019-01-07  189.210968   53.796001  156.295288  156.524857   86.748817   
2019-01-08  190.627838   54.268501  155.718063  157.276382   86.585228   
...                ...         ...         ...         ...         ...   
2021-12-27  542.369263  147.906494  366.451324  383.501495  147.970337   
2021-12-28  543.495483  146.686996  366.045166  385.523010  148.419434   
2021-12-29  546.508179  146.654999  364.713715  389.907593  148.344559   
2021-12-30  542.792786  146.200500  364.071442  389.053406  148.269714   
2021-12-31  546.440918  144.852005  361.266724  393.865143  148.148102   

                   LMT          MA        MSFT        NFLX        NVDA  \
Date                                                                     
2019-01-02  231.686234  184.257751   95.846008  267.660004   33.790482   
2019-01-03  225.866272  175.945053   92.320045  271.200012   31.748959   
2019-01-04  231.957565  184.277176   96.613777  297.570007   33.783031   
2019-01-07  234.618088  185.694992   96.736992  315.339996   35.571541   
2019-01-08  236.184647  187.047134   97.438416  320.269989   34.685978   
...                ...         ...         ...         ...         ...   
2021-12-27  332.307373  355.478638  335.668427  613.119995  309.023804   
2021-12-28  335.599365  355.942291  334.492188  610.710022  302.802399   
2021-12-29  336.092682  356.445496  335.178345  610.539978  299.596802   
2021-12-30  335.438049  356.149506  332.600342  612.090027  295.452484   
2021-12-31  337.174164  354.501892  329.659790  602.440002  293.704926   

                   TGT         UNH           V  
Date                                            
2019-01-02   58.623016  225.958511  128.224472  
2019-01-03   57.820080  219.796661  123.603668  
2019-01-04   58.614197  222.367188  128.928650  
2019-01-07   61.481815  222.794083  131.253540  
2019-01-08   61.420044  225.772980  131.967407  
...                ...         ...         ...  
2021-12-27  211.016037  485.869049  213.895538  
2021-12-28  211.778717  489.215179  214.308334  
2021-12-29  214.612961  491.783142  214.426239  
2021-12-30  218.370041  490.664490  214.131409  
2021-12-31  217.927490  488.437042  212.991318  

[757 rows x 18 columns]

In [215]:
#set parameters to calculate predict market drop
market_drop_info = pd.read_excel("MarketDD.xlsx",index_col=0)
swan_to_predict=9
total_day=yahooDataFrame.shape[0]
t1=int(round(market_drop_info.loc[:end_swan,"T1"].mean(),0))
t1=int((np.array(market_drop_info.loc[:end_swan,"T1"])*np.array(weight_swan)).sum())
#t2=total_day-t1
t2=int(round(market_drop_info.loc[:end_swan,"T2"].mean(),0))
dd=market_drop_info.loc[:end_swan,"Actual DD"].mean()
t0=int(total_day-t1-t2)

In [216]:
#calculate predict market drop
md = [] #Make market drop data list named md


j = 0 #Start from 0
inc = dd/(t1-1) #Calculate unit increasing market drop
for i in range(t1): #Append market drop data for t1
    md.append(round(j,4))
    j = j + inc

base = (t2+1)**(1/(dd*100)) #Calculate log base
l1 = [] #Make decreasing market drop list
for i in range(t2):
    l1.append(math.log((i+2),base)/100)

for i in range(t2): #Append market drop data for t2
    md.append(round((dd-l1[i]),4))

for i in range(t0):
    md.append(0)

market_drop = pd.DataFrame(md) #Change list into dataframe
#market_drop = market_drop.rename(columns={0: 'Swan Drop spy'}) #Change column name
market_drop1 = pd.read_csv("trainingMarketdrop.csv")

In [217]:
market_drop.to_csv("market_drop.csv")

In [218]:
market_drop

0
0    0.0000
1    0.0040
2    0.0080
3    0.0119
4    0.0159
..      ...
752  0.0000
753  0.0000
754  0.0000
755  0.0000
756  0.0000

[757 rows x 1 columns]

In [219]:
swan_drop_pct=np.array(swan_beta)*np.array(market_drop)
yahooDataFrame=pd.DataFrame((1-swan_drop_pct)*np.array(yahooDataFrame),index=yahooDataFrame.index,columns=yahooDataFrame.columns)

In [220]:
yahooDataFrame

AAPL        ADBE        AMZN        BAC       BRK-B  \
Date                                                                    
2019-01-02   37.845036  224.570007   76.956497  22.099756  202.800003   
2019-01-03   34.002704  214.735546   74.737334  21.663838  190.561231   
2019-01-04   35.378436  224.167293   78.188466  22.478407  192.961863   
2019-01-07   35.225950  226.210377   80.581522  22.377868  193.551614   
2019-01-08   35.820387  228.544509   81.614682  22.249173  191.836411   
...                ...         ...         ...        ...         ...   
2021-12-27  178.065643  577.679993  169.669495  42.306969  296.670013   
2021-12-28  177.038712  569.359985  170.660995  42.363827  298.290009   
2021-12-29  177.127594  569.289978  169.201004  42.297478  299.459991   
2021-12-30  175.962418  570.530029  168.644501  42.202713  299.980011   
2021-12-31  175.340317  567.059998  166.716995  42.164803  299.000000   

                  COST       GOOGL          GS          HD         JPM  \
Date                                                                     
2019-01-02  187.163452   52.734001  152.752380  152.431381   84.811691   
2019-01-03  182.128558   51.103381  150.061589  148.715831   83.139975   
2019-01-04  186.318524   53.545812  154.497959  152.768239   85.721408   
2019-01-07  185.929712   53.265002  154.895294  155.413116   85.309189   
2019-01-08  186.210808   53.552783  153.854391  155.783815   84.665318   
...                ...         ...         ...         ...         ...   
2021-12-27  542.369263  147.906494  366.451324  383.501495  147.970337   
2021-12-28  543.495483  146.686996  366.045166  385.523010  148.419434   
2021-12-29  546.508179  146.654999  364.713715  389.907593  148.344559   
2021-12-30  542.792786  146.200500  364.071442  389.053406  148.269714   
2021-12-31  546.440918  144.852005  361.266724  393.865143  148.148102   

                   LMT          MA        MSFT        NFLX        NVDA  \
Date                                                                     
2019-01-02  231.686234  184.257751   95.846008  267.660004   33.790482   
2019-01-03  224.643089  175.519548   91.958662  270.228374   31.595140   
2019-01-04  229.445224  183.385865   95.857394  295.437778   33.455685   
2019-01-07  230.838116  184.358966   95.610438  311.978901   35.058834   
2019-01-08  231.100374  185.249025   95.922273  315.708903   34.017987   
...                ...         ...         ...         ...         ...   
2021-12-27  332.307373  355.478638  335.668427  613.119995  309.023804   
2021-12-28  335.599365  355.942291  334.492188  610.710022  302.802399   
2021-12-29  336.092682  356.445496  335.178345  610.539978  299.596802   
2021-12-30  335.438049  356.149506  332.600342  612.090027  295.452484   
2021-12-31  337.174164  354.501892  329.659790  602.440002  293.704926   

                   TGT         UNH           V  
Date                                            
2019-01-02   58.623016  225.958511  128.224472  
2019-01-03   57.475312  219.480929  123.323343  
2019-01-04   57.915191  221.728337  128.343846  
2019-01-07   60.391175  221.841968  130.367958  
2019-01-08   59.964266  224.483817  130.777715  
...                ...         ...         ...  
2021-12-27  211.016037  485.869049  213.895538  
2021-12-28  211.778717  489.215179  214.308334  
2021-12-29  214.612961  491.783142  214.426239  
2021-12-30  218.370041  490.664490  214.131409  
2021-12-31  217.927490  488.437042  212.991318  

[757 rows x 18 columns]

In [221]:
yahooDataFrame=yahooDataFrame.dropna(how="all",axis = 1)
selected_stock_list=yahooDataFrame.columns.values
selected_stock_number = yahooDataFrame.shape[1]
selected_stock_list

array(['AAPL', 'ADBE', 'AMZN', 'BAC', 'BRK-B', 'COST', 'GOOGL', 'GS',
       'HD', 'JPM', 'LMT', 'MA', 'MSFT', 'NFLX', 'NVDA', 'TGT', 'UNH',
       'V'], dtype=object)

# Step3 - MVO

In [222]:
#Set the paramter for MVO process
Portfolio_Date=end

In [223]:
#data cleaning - filling missing data in yahooDataFrame
data_cleaning(yahooDataFrame)

In [224]:
bond_yield = quandl.get('FRED/DGS3MO')
bond_yield=np.log(bond_yield/100+1)
date=list(map(str,bond_yield.index.values))
date=list(map(modify_date,date))
week=pd.to_datetime(date).strftime("%W").values
week_1=np.roll(week,1)
week_difference=np.where(week!=week_1)
week_difference=np.delete(week_difference,0,None)
rf_week=bond_yield.iloc[week_difference-1]

LimitExceededError: (Status 429) (Quandl Error QELx01) You have exceeded the anonymous user limit of 50 calls per day. To make more calls today, please register for a free Nasdaq Data Link account and then include your API key with your requests.

In [225]:
# Calculated R for 1 year and 0.5 year
today_price = yahooDataFrame.iloc[-MA_days:,:]
one_year_ago_data = get_price_years_ago(yahooDataFrame,end,1)
one_year_ago_date = one_year_ago_data.index.values[-1]
half_year_ago_data = get_price_years_ago(yahooDataFrame,end,0.5)
half_year_ago_date = half_year_ago_data.index.values[-1]
one_year_ago_price=yahooDataFrame.loc[one_year_ago_date:,:]
one_year_ago_price=yahooDataFrame.iloc[:MA_days,:]
half_year_ago_price=yahooDataFrame.loc[half_year_ago_date:,:]
half_year_ago_price=yahooDataFrame.iloc[:MA_days,:]

R_mv_one_year=np.mean(pd.DataFrame(np.array(today_price)/np.array(one_year_ago_price)-1,index=today_price.index,columns=today_price.columns),axis=0)
R_mv_half_year=np.mean(pd.DataFrame(np.array(today_price)/np.array(half_year_ago_price)-1,index=today_price.index,columns=today_price.columns),axis=0)



In [226]:
R_mv_one_year.index

Index(['AAPL', 'ADBE', 'AMZN', 'BAC', 'BRK-B', 'COST', 'GOOGL', 'GS', 'HD',
       'JPM', 'LMT', 'MA', 'MSFT', 'NFLX', 'NVDA', 'TGT', 'UNH', 'V'],
      dtype='object')

In [227]:
# Calculate MA
MA_Data=yahooDataFrame.rolling(MA_days).mean().dropna(axis=0)
MA_Data=MA_Data.loc[one_year_ago_date:,:]
MA_now = MA_Data.iloc[-1,:]
MA_one_year_ago = MA_Data.iloc[0,:]
MA_half_year_ago = MA_Data.loc[half_year_ago_date,:]

In [228]:
# Calculate daily return
daily_return = yahooDataFrame.pct_change().dropna()
log_daily_return = np.log(1+daily_return)

# Get week end stock price data
stock_date = yahooDataFrame.index.values
week=pd.to_datetime(stock_date).strftime("%W").values
week_1=np.roll(week,1)
week_difference=np.where(week!=week_1)
week_difference=np.delete(week_difference,0,None)
# Calculate weekly return

weekly_return=yahooDataFrame.iloc[week_difference-1].pct_change().dropna()
log_weekly_return = np.log(1+weekly_return)

# Get month end stock price data
stock_date = yahooDataFrame.index.values
month=pd.to_datetime(stock_date).strftime("%m").values
month_1=np.roll(month,1)
month_difference=np.where(month!=month_1)
month_difference=np.delete(month_difference,0,None)
# Calculate monthly return
monthly_return=yahooDataFrame.iloc[month_difference-1].pct_change().dropna()
log_monthly_return = np.log(1+monthly_return)

# Get semi-month end stock price data
semi_month = []
for i in range(1,len(month_difference)):
    semi_month.append((month_difference[i]-month_difference[i-1])//2+month_difference[i-1])
    semi_month.append(month_difference[i]-1)
# Calculate semi-monthly return
semi_monthly_return=yahooDataFrame.iloc[semi_month].pct_change().dropna()
log_semi_monthly_return = np.log(1+semi_monthly_return)

In [229]:
# Calculated Max Dropdown for each stock
stock_return_one_year=daily_return.loc[one_year_ago_date:,:]
mdd=[]
for column in stock_return_one_year.columns:
    mdd .append(max_drawdown_absolute(stock_return_one_year.loc[:,column]))
mdd=pd.DataFrame(mdd,index = stock_return_one_year.columns,columns=["MAXDD","start_index","end_index"])
mar=R_mv_one_year/mdd.iloc[:,0]

In [230]:
#calculate weekly sd for each stock
one_year_weekly_return=log_weekly_return.iloc[log_weekly_return.index >= one_year_ago_date]
weekly_std= np.std(one_year_weekly_return)*np.sqrt(one_year_weekly_return.shape[0])

#Calculate garch_std sd for each stock
one_year_monthly_return=log_monthly_return.iloc[log_monthly_return.index >= one_year_ago_date]
res_all = one_year_monthly_return - np.mean(one_year_monthly_return)
judge = one_year_monthly_return.shape[0]
for stock in one_year_monthly_return.columns:
    res=res_all[stock]
    h= het_arch(res)
    if judge < 100 or h ==0:
        garch_std = weekly_std

    else:#build Garch Model
        std = []
        if judge <=200:
            p = 0
            q = 6
        else:
            p = 1
            q = 1

        std.append(fit_garch(one_year_monthly_return[stock],p,q))
        garch_std = pd.DataFrame(std,index = one_year_monthly_return.columns)

#Calculate monthly sd for each stock
one_year_monthly_return=log_monthly_return.iloc[log_monthly_return.index >= one_year_ago_date]
monthly_std = np.std(one_year_monthly_return)*np.sqrt(12);

#Calculate semi_monthly sd for each stock
one_year_semi_monthly_return=log_semi_monthly_return.iloc[log_semi_monthly_return.index >= one_year_ago_date]
semi_monthly_std = np.std(one_year_semi_monthly_return)*np.sqrt(24);


Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.
Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


/Users/wenyiye/anaconda3/lib/python3.11/site-packages/numpy/core/fromnumeric.py:3643: FutureWarning: The behavior of DataFrame.std with axis=None is deprecated, in a future version this will reduce over both axes and return a scalar. To retain the old behavior, pass axis=0 (or do not pass axis)
  return std(axis=axis, dtype=dtype, out=out, ddof=ddof, **kwargs)


In [231]:
# Calculated MaxDrop
DD_range = 90
total_range = 90
DD_end = yahooDataFrame.iloc[yahooDataFrame.index <= one_year_ago_date]
DD_start = yahooDataFrame.iloc[yahooDataFrame.index <= end-datetime.timedelta(total_range)]
max_DD=[-1]*selected_stock_number


if (DD_start.shape[0] != 1 ) and (DD_end.shape[0] != 1):
    DD_start = DD_start.index[-1]
    DD_end = DD_end.index[-1]
    while DD_start > DD_end :
        DD_start = yahooDataFrame.iloc[yahooDataFrame.index <= end-datetime.timedelta(total_range)]
        DD_mid = yahooDataFrame.iloc[yahooDataFrame.index <= end-datetime.timedelta(DD_range+total_range)]
        if (DD_start.shape[0] != 1 ) and (DD_mid.shape[0] != 1):
            DD_start = DD_start.index[-1]
            DD_mid = DD_mid.index[-1]
            price = yahooDataFrame.loc[DD_start:DD_mid,:]
            for i in range(len(yahooDataFrame.columns)):
                max_DD[i]=max(max_DD[i],max_drawdown_absolute(stock_return_one_year.iloc[:,i])[0])
            total_range = total_range + 1
        else:
            break

In [232]:
# Read OPT-data
optdata = pd.read_excel("optdata.xlsx",index_col=0,sheet_name = 1)
P_current = MA_now
P_fwd = optdata.P_fwd.loc[P_current.index]
R_fwd=P_fwd/P_current-1
R_60 = P_current/MA_one_year_ago - 1
R_60_half = P_current/MA_half_year_ago - 1
R_MA_1ago = R_mv_one_year
R_MA_halfago = R_mv_half_year
Rfwd_adjusted = pd.Series(index=R_MA_1ago.index)
for i in R_fwd.index:
    if R_fwd[i] < 0.5*R_60[i]:
        Rfwd_adjusted[i] = R_60_half[i]
    elif R_fwd[i] > 1.3*R_60[i]:
        if 1.3*R_60[i] > 0.7*R_fwd[i]:
            Rfwd_adjusted[i] = 1.3*R_60[i]
        else:
            Rfwd_adjusted[i] = 0.7*R_fwd[i]
    else:
        Rfwd_adjusted[i] = R_fwd[i]
Rfwd_adjusted[Rfwd_adjusted<0]=0

In [233]:
price_now = today_price.iloc[-1,:]
optimizer = optdata.loc[P_current.index,:]
FFC = pd.DataFrame([R_MA_1ago.values,R_MA_halfago.values,MA_now.values,price_now.values,semi_monthly_std.values,weekly_std.values,MA_one_year_ago.values,MA_half_year_ago.values,max_DD,R_60.values,R_60_half.values,P_fwd.values,Rfwd_adjusted.values],columns = R_MA_1ago.index,index = ["R_MA_1ago","R_MA_halfago","MA_now","price",'std','std_f','MA_1ago','MA_halfago','Fall_MDD','R_60','R_60_half','R_fwd',"Rfwd_adjusted"]).T
preselected_stock = preselected_stock.loc[selected_stock_list,:]
preselected_stock["Rfwd_adjusted"]=Rfwd_adjusted.values
preselected_stock["std_f"]=weekly_std.values
preselected_stock["SR"]=preselected_stock["Rfwd_adjusted"]/preselected_stock["std_f"]
preselected_stock["PR_SR"]=preselected_stock["PR"]*preselected_stock["SR"]**0.5
preselected_stock.to_csv("preselected_Stocks_info.csv")
p=FFC.MA_now
EPS_fwd=optimizer.EPS_fwd
EPS_ttm=optimizer.EPS_ttm
fall=FFC.Fall_MDD
FFC.to_csv("WEDataBank.csv")

PE=p/EPS_fwd
PEG= p/(EPS_fwd*(EPS_fwd/EPS_ttm-1))
PEG[PEG<0]=2000


In [234]:
preselected_stock

Swan4     Swan5     Swan6     Swan7     Swan8     Swan9   Swan10a  \
Ticker                                                                         
AAPL    1.345472  0.858909  0.279703  1.582785  1.829198  0.972646  0.955996   
ADBE    1.599366  1.393154  1.278684  0.687330  1.210366  0.628947  1.680628   
AMZN   -0.445606  0.328167  0.123350  0.334033  1.561997  0.390752  1.440979   
BAC     0.594106  2.142401  2.667373  1.184257  1.192921  1.509426  1.144357   
BRK-B   0.220942  1.172896  0.533684  0.870710  0.663086  0.928445 -0.420873   
COST    0.829818  0.976294 -0.015790  0.618966  0.918643  0.368083  0.536185   
GOOGL        NaN  0.803565  1.167641  0.870361  0.938163  0.979057  0.880849   
GS      1.029728  1.064879  1.959793  1.207118  1.557229  1.356818  1.301592   
HD      1.546126  0.638987  0.756432  0.161429  1.098092  1.043489  1.605762   
JPM     1.649017  1.453522  1.887942  1.012903  0.969233  1.348489  1.440874   
LMT     0.009892  1.091646  0.569952  0.224948  1.448131  1.138289 -1.969023   
MA           NaN  0.644202  0.061049  0.805387  1.084036  1.300211  1.081897   
MSFT    0.870338  0.976788  0.607971  0.988753  0.897603  0.868731  1.244157   
NFLX         NaN -0.513562  3.473958  0.612869  1.902424  0.212860  3.055209   
NVDA    2.545656  0.635717  1.251062 -0.253400  2.787430  1.026747  2.039407   
TGT     1.178804  1.162603  0.421476  0.869800  1.393401  0.559241  0.684464   
UNH    -0.619292  0.706054  1.079657  0.775080  0.688288  1.138551  0.409690   
V            NaN  0.578961  0.335963  0.580043  0.919773  1.153300  0.948281   

             avg        PR  Rfwd_adjusted     std_f         SR     PR_SR  
Ticker                                                                    
AAPL    1.117816 -0.117816       0.578740  0.239959   2.411830 -0.182968  
ADBE    1.211211 -0.211211       0.153273  0.302558   0.506590 -0.150329  
AMZN    0.533381  0.466619       9.058544  0.241910  37.445897  2.855381  
BAC     1.490692 -0.490692       0.084898  0.246937   0.343806 -0.287717  
BRK-B   0.566984  0.433016       0.017195  0.142329   0.120813  0.150508  
COST    0.604600  0.395400       0.419931  0.191225   2.196008  0.585941  
GOOGL   0.939939  0.060061       6.547853  0.242882  26.958963  0.311848  
GS      1.353880 -0.353880       0.052422  0.262662   0.199578 -0.158093  
HD      0.978617  0.021383       0.308801  0.232805   1.326433  0.024627  
JPM     1.394569 -0.394569       0.018724  0.212973   0.087917 -0.116993  
LMT     0.359119  0.640881       0.242576  0.203677   1.190986  0.699408  
MA      0.829464  0.170536       0.000000  0.263515   0.000000  0.000000  
MSFT    0.922049  0.077951       0.298254  0.197170   1.512676  0.095873  
NFLX    1.457293 -0.457293       0.233542  0.287682   0.811808 -0.412023  
NVDA    1.433231 -0.433231       0.714120  0.400732   1.782039 -0.578334  
TGT     0.895684  0.104316       0.020756  0.239791   0.086557  0.030690  
UNH     0.596861  0.403139       0.179483  0.199298   0.900579  0.382574  
V       0.752720  0.247280       0.000000  0.237327   0.000000  0.000000

In [235]:
cov = pd.DataFrame(np.cov(np.exp(one_year_weekly_return)-1,rowvar=False,bias = False)*51,index= one_year_weekly_return.columns, columns= one_year_weekly_return.columns)
E_2 = Rfwd_adjusted/fall
E_3 = Rfwd_adjusted/PEG
E_4 = Rfwd_adjusted
std =  np.std(np.exp(one_year_weekly_return)-1)*np.sqrt(52)


Intel MKL WARNING: Support of Intel(R) Streaming SIMD Extensions 4.2 (Intel(R) SSE4.2) enabled only processors has been deprecated. Intel oneAPI Math Kernel Library 2025.0 will require Intel(R) Advanced Vector Extensions (Intel(R) AVX) instructions.


/Users/wenyiye/anaconda3/lib/python3.11/site-packages/numpy/core/fromnumeric.py:3643: FutureWarning: The behavior of DataFrame.std with axis=None is deprecated, in a future version this will reduce over both axes and return a scalar. To retain the old behavior, pass axis=0 (or do not pass axis)
  return std(axis=axis, dtype=dtype, out=out, ddof=ddof, **kwargs)


# Optimization

In [236]:
w0 = 1/selected_stock_number*np.ones(selected_stock_number)
uplim_ini = np.zeros(selected_stock_number)
uplim3 =pd.DataFrame( w1*(1-uplim_ini) + w2 * uplim_ini,index = std.index,columns=["weight"])
for i in uplim3.index:
    if i in ["SPY","IWD"]:
        uplim3.loc[i,:]=0
low_lim =  np.zeros(selected_stock_number)
multi=lambda x: x.T @cov@x

In [237]:
if method == "gptLowest8":
    cleaned_weights =  {'AMZN': 0.056, 'AAPL': 0.056, 'MSFT': 0.056, 'GOOGL': 0.056,
                  'NVDA': 0.056, 'NFLX': 0.056, 'MA': 0.056, 'V': 0.056,
                  'UNH': 0.056, 'JPM': 0.056, 'GS': 0.056, 'COST': 0.056,
                  'HD': 0.056, 'TGT': 0.056, 'ADBE': 0.056, 'BAC': 0.056,
                  'LMT': 0.056, 'BRK-B': 0.056}
    
else:
    ef = EfficientFrontier(E_2/100, cov,weight_bounds=(0, w1))
    #ef.add_constraint(lambda w: w@E_2== 12)
    raw_weights = ef.max_sharpe(0.01)
    cleaned_weights = ef.clean_weights()
    ef.portfolio_performance(verbose=True)
    
print(cleaned_weights)

Expected annual return: 25.2%
Annual volatility: 11.5%
Sharpe Ratio: 2.11
OrderedDict([('AAPL', 0.0), ('ADBE', 0.0), ('AMZN', 0.17), ('BAC', 0.0), ('BRK-B', 0.14176), ('COST', 0.11802), ('GOOGL', 0.17), ('GS', 0.0), ('HD', 0.0), ('JPM', 0.09796), ('LMT', 0.11963), ('MA', 0.0), ('MSFT', 0.0), ('NFLX', 0.00478), ('NVDA', 0.0), ('TGT', 0.00784), ('UNH', 0.17), ('V', 0.0)])


/Users/wenyiye/anaconda3/lib/python3.11/site-packages/pypfopt/efficient_frontier/efficient_frontier.py:441: UserWarning: The risk_free_rate provided to portfolio_performance is different to the one used by max_sharpe. Using the previous value.
  warnings.warn(


In [238]:
weight1=np.array(pd.DataFrame(cleaned_weights.values(), index = list(cleaned_weights),columns = ["weight"]))[:,0]

In [239]:
sd1 = np.sqrt(weight1@cov@weight1.T)
R1 = weight1.T@E_2/100
sharpe_ratio1 = (R1-0.01)/sd1
print("new_sharpe:",sharpe_ratio1)

new_sharpe: 2.1096492834059033


weight2 =   pd.read_excel("old_weight.xlsx",index_col=0)
weight2=np.array(weight2.loc[list(cleaned_weights),:])[:,0]

sd2 = np.sqrt(weight2@cov@weight2.T)
R2 = weight2.T@E_2/100
sharpe_ratio2 = (R2-0.01)/sd2
print("old_sharpe:",sharpe_ratio2)

In [240]:
weight = pd.DataFrame(cleaned_weights.values(), index=list(cleaned_weights), columns=["weight"])
weight = weight[weight.weight >= 0.03]
weight.weight = weight.weight / sum(weight.weight)
weight.to_csv("weights.csv")

See pyportfolioopt.readthedocs.io/en/latest/MeanVariance.html for more reference


In [241]:
if stock_type == "S&P100":
    OEX=pdr.get_data_yahoo("^OEX", start=start_swan_date, end=end_swan_date)["Adj Close"]

elif stock_type == "S&P500":
    OEX=pdr.get_data_yahoo("SPY", start=start_swan_date, end=end_swan_date)["Adj Close"]

stock_price=pdr.get_data_yahoo(list(weight.index), start=start_swan_date, end=end_swan_date)["Adj Close"]

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  7 of 7 completed


In [242]:
stock_price.to_csv("tradeinfo.csv")
stock_price

AMZN       BRK-B        COST       GOOGL         JPM  \
Date                                                                     
2022-01-03  170.404495  300.790009  545.488037  144.991501  151.282242   
2022-01-04  167.522003  308.529999  543.100952  144.399506  157.017334   
2022-01-05  164.356995  309.920013  529.326660  137.774994  154.146729   
2022-01-06  163.253998  313.220001  529.211243  137.747498  155.784393   
2022-01-07  162.554001  319.779999  516.101196  137.016998  157.327927   
...                ...         ...         ...         ...         ...   
2022-12-23   85.250000  306.489990  448.304230   89.230003  126.698761   
2022-12-27   83.040001  305.549988  444.282928   87.389999  127.142708   
2022-12-28   81.820000  303.429993  438.943726   86.019997  127.837593   
2022-12-29   84.180000  309.059998  442.374023   88.449997  128.571045   
2022-12-30   84.000000  308.899994  442.344910   88.230003  129.420349   

                   LMT         UNH  
Date                                
2022-01-03  336.178009  488.573212  
2022-01-04  343.416534  477.503723  
2022-01-05  339.764099  476.326782  
2022-01-06  339.631256  456.833618  
2022-01-07  341.661560  446.085205  
...                ...         ...  
2022-12-23  470.532135  523.429626  
2022-12-27  472.683807  524.099609  
2022-12-28  470.464020  520.612122  
2022-12-29  474.192902  522.020935  
2022-12-30  473.647705  522.316406  

[251 rows x 7 columns]

In [243]:
start=stock_price.loc["2022-01-03"]
end = stock_price.loc["2022-10-12"]
stock_drop=abs(end/start-1)
market_drop = abs(OEX.loc["2022-10-12"]/OEX.loc["2022-01-03"]-1)

In [244]:
beta = stock_drop/market_drop
1-beta.T@weight

weight    0.248632
dtype: float64

In [245]:
stock_drop

AMZN     0.337459
BRK-B    0.122311
COST     0.173026
GOOGL    0.327133
JPM      0.339021
LMT      0.143832
UNH      0.005030
dtype: float64

In [246]:
print(stock_price.head(1))
weight

                  AMZN       BRK-B        COST       GOOGL         JPM  \
Date                                                                     
2022-01-03  170.404495  300.790009  545.488037  144.991501  151.282242   

                   LMT         UNH  
Date                                
2022-01-03  336.178009  488.573212  


weight
AMZN   0.172175
BRK-B  0.143573
COST   0.119530
GOOGL  0.172175
JPM    0.099213
LMT    0.121160
UNH    0.172175

In [247]:
a=stock_price@weight
b=1-a.loc["2022-10-12"]/a.loc["2022-01-03"]
1-b/market_drop

weight    0.594123
dtype: float64

In [248]:
injected_result = pd.DataFrame(index = stock_price.index)
S1 = np.array(10000*weight.T)/np.array(stock_price.iloc[0,:]).T


In [249]:
portfolio_value = np.sum(np.array(weight.T) * stock_price,axis=1)
S1 = np.array(10000*weight.T)/np.array(stock_price.iloc[0,:]).T
injected_result["portfolio_value"]=stock_price@S1.T
S2 = 10000/float(OEX[0])
injected_result["oex"]=S2*OEX
injected_result.to_csv("Injected_result.csv")

/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_46265/2729638000.py:4: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  S2 = 10000/float(OEX[0])


In [251]:
temp=injected_result.loc[["2022-01-03","2022-10-12"]]
Portfolio_DD=abs(temp['portfolio_value'][1]/temp['portfolio_value'][0]-1)
DD=abs(temp['oex'][1]/temp['oex'][0]-1)
PR=1-(Portfolio_DD/DD)
print(PR)
temp
DD

0.3829905043103061


/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_46265/2994947419.py:2: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  Portfolio_DD=abs(temp['portfolio_value'][1]/temp['portfolio_value'][0]-1)
/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_46265/2994947419.py:3: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  DD=abs(temp['oex'][1]/temp['oex'][0]-1)


0.2722984138075022

In [194]:
allocation=pd.read_excel('allocation weight.xlsx',index_col='stock selected')
dfMVOstock=deepcopy(weight)
dfMVOstock['PR_SR']=''
dfMVOstock['SR']=''
for i in range(len(weight)):
    dfMVOstock.iloc[i,1]=preselected_stock.loc[weight.index[i],'PR_SR']
    dfMVOstock.iloc[i,2]=preselected_stock.loc[weight.index[i],'SR']
dfMVOstock_sort=dfMVOstock.sort_values(by='PR_SR',ascending=False)
postallocationweight=post_allocation(dfMVOstock_sort)
postallocationweight


/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_46265/2775426837.py:12: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  if (dfMVOweight.iloc[i,4]+residual/(numofstocks-i))>allocationweight[0]:
/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_46265/2775426837.py:13: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  dfMVOweight.iloc[i,5]=allocationweight[0]
/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_46265/2775426837.py:17: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFram

weight     PR_SR         SR     equal proportion adjusted proportion  \
AMZN   0.055556  2.855381  37.445897  0.055556   0.878472                0.07   
LMT    0.055556  0.699408   1.190985  0.055556   0.215176                0.07   
COST   0.055556  0.585941   2.196005  0.055556   0.180268                0.07   
UNH    0.055556  0.382574   0.900578  0.055556   0.117701                0.07   
GOOGL  0.055556  0.311848  26.958963  0.055556   0.095941                0.07   
BRK-B  0.055556  0.150508   0.120813  0.055556   0.046305                0.07   
MSFT   0.055556  0.095873   1.512674  0.055556   0.029496                0.07   
TGT    0.055556   0.03069   0.086557  0.055556   0.009442                0.07   
HD     0.055556  0.024627   1.326435  0.055556   0.007577                0.07   
MA     0.055556       0.0        0.0  0.055556        0.0                0.07   
V      0.055556       0.0        0.0  0.055556        0.0                0.07   
JPM    0.055556 -0.116993   0.087917  0.055556  -0.035993                0.07   
ADBE   0.055556 -0.150329    0.50659  0.055556   -0.04625                0.07   
GS     0.055556 -0.158093   0.199578  0.055556  -0.048638            0.068989   
AAPL   0.055556 -0.182968   2.411831  0.055556  -0.056291            0.061336   
BAC    0.055556 -0.287717   0.343805  0.055556  -0.088517             0.02911   
NFLX   0.055556 -0.412023   0.811808  0.055556  -0.126761           -0.009134   
NVDA   0.055556 -0.578334   1.782039  0.055556  -0.177927             -0.0603   

       direct  
AMZN     0.07  
LMT      0.07  
COST     0.07  
UNH      0.07  
GOOGL    0.07  
BRK-B    0.07  
MSFT     0.07  
TGT      0.07  
HD       0.07  
MA       0.07  
V      0.0375  
JPM    0.0375  
ADBE   0.0375  
GS     0.0375  
AAPL   0.0375  
BAC    0.0375  
NFLX   0.0375  
NVDA   0.0375

In [125]:
#draw type E graph for postallocation
MVOweight=postallocationweight['weight']
equalweight=postallocationweight['equal']
proportionweight=postallocationweight['adjusted proportion']
directweight=postallocationweight['direct']
output(MVOweight).to_csv('no_post_allocation_result.csv')
output(equalweight).to_csv('equal_weight_result.csv')
output(proportionweight).to_csv('proportional_weight_result.csv')
output(directweight).to_csv('direct_weight_result.csv')

[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  8 of 8 completed
[*********************100%%**********************]  1 of 1 completed


/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_46265/1728796536.py:14: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  S2 = 10000/float(OEX[0])


[*********************100%%**********************]  8 of 8 completed


/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_46265/1728796536.py:14: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  S2 = 10000/float(OEX[0])


[*********************100%%**********************]  1 of 1 completed
[*********************100%%**********************]  8 of 8 completed
[*********************100%%**********************]  1 of 1 completed


/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_46265/1728796536.py:14: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  S2 = 10000/float(OEX[0])


[*********************100%%**********************]  8 of 8 completed


/var/folders/6g/__5vs7k9339d_y5ztlb880wm0000gn/T/ipykernel_46265/1728796536.py:14: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  S2 = 10000/float(OEX[0])
